# Ensuring Consistency with ACID Transactions with Delta Lake (Loan Risk Data)

<img src="https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-logo-whitebackground.png" width=200/>

This is a companion notebook to provide a Delta Lake example against the Lending Club data.
* This notebook has been tested with *DBR 9 ML, Python 3*
* For the bottom sections of this notebook, you will need `mlflow` and `yellowbrick` installed on your cluster as well

## The Data

The data used is public data from Lending Club. It includes all funded loans from 2012 to 2017. Each loan includes applicant information provided by the applicant as well as the current loan status (Current, Late, Fully Paid, etc.) and latest payment information. For a full view of the data please view the data dictionary available [here](https://resources.lendingclub.com/LCDataDictionary.xlsx).


![Loan_Data](https://preview.ibb.co/d3tQ4R/Screen_Shot_2018_02_02_at_11_21_51_PM.png)

https://www.kaggle.com/wendykan/lending-club-loan-data

## ![Delta Lake Tiny Logo](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Delta Lake

Optimization Layer a top blob storage for Reliability (i.e. ACID compliance) and Low Latency of Streaming + Batch data pipelines.

## Import Data and create pre-Delta Lake Table
* This will create a lot of small Parquet files emulating the typical small file problem that occurs with streaming or highly transactional data

In [0]:
# -----------------------------------------------
# Uncomment and run if this folder does not exist
# -----------------------------------------------
# Configure location of loanstats_2012_2017.parquet
lspq_path = "/databricks-datasets/samples/lending_club/parquet/"

# Read loanstats_2012_2017.parquet
data = spark.read.parquet(lspq_path)

# Reduce the amount of data (to run on DBCE)
(loan_stats, loan_stats_rest) = data.randomSplit([0.01, 0.99], seed=123)

# Select only the columns needed
loan_stats = loan_stats.select("addr_state", "loan_status")

# Create loan by state
loan_by_state = loan_stats.groupBy("addr_state").count()

# Create table
loan_by_state.createOrReplaceTempView("loan_by_state")

# Display loans by state
display(loan_by_state)

addr_state count AZ 355 SC 172 LA 208 MN 254 NJ 553 DC 47 OR 178 VA 414 RI 56 KY 133 WY 26 NH 67 MI 383 NV 206 WI 187 ID 19 CA 1994 CT 215 NE 28 MT 40 NC 420 VT 28 MD 360 DE 44 MO 269 IL 575 ME 18 WA 293 ND 21 MS 66 AL 182 IN 264 OH 519 TN 224 NM 85 PA 479 SD 33 NY 1179 TX 1260 WV 30 GA 470 MA 303 KS 121 FL 1061 CO 308 AK 26 AR 113 OK 139 UT 88 HI 79

Output can only be rendered in Databricks

## ![Delta Lake Tiny Logo](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Easily Convert Parquet to Delta Lake format
With Delta Lake, you can easily transform your Parquet data into Delta Lake format.

In [0]:
lc_path = "/databricks-datasets/delta-sharing/samples/lending_club/"

In [0]:
df = spark.read.format("delta").load(lc_path)
display(df)

id member_id loan_amnt funded_amnt funded_amnt_inv term int_rate installment grade sub_grade emp_title emp_length home_ownership annual_inc verification_status loan_status pymnt_plan url desc purpose title zip_code addr_state dti delinq_2yrs earliest_cr_line inq_last_6mths mths_since_last_delinq mths_since_last_record open_acc pub_rec revol_bal revol_util total_acc initial_list_status out_prncp out_prncp_inv total_pymnt total_pymnt_inv total_rec_prncp total_rec_int total_rec_late_fee recoveries collection_recovery_fee last_pymnt_d last_pymnt_amnt next_pymnt_d last_credit_pull_d collections_12_mths_ex_med mths_since_last_major_derog policy_code application_type annual_inc_joint dti_joint verification_status_joint acc_now_delinq tot_coll_amt tot_cur_bal open_acc_6m open_il_6m open_il_12m open_il_24m mths_since_rcnt_il total_bal_il il_util open_rv_12m open_rv_24m max_bal_bc all_util total_rev_hi_lim inq_fi total_cu_tl inq_last_12m acc_open_past_24mths avg_cur_bal bc_open_to_buy bc_util chargeoff_within_12_mths delinq_amnt mo_sin_old_il_acct mo_sin_old_rev_tl_op mo_sin_rcnt_rev_tl_op mo_sin_rcnt_tl mort_acc mths_since_recent_bc mths_since_recent_bc_dlq mths_since_recent_inq mths_since_recent_revol_delinq num_accts_ever_120_pd num_actv_bc_tl num_actv_rev_tl num_bc_sats num_bc_tl num_il_tl num_op_rev_tl num_rev_accts num_rev_tl_bal_gt_0 num_sats num_tl_120dpd_2m num_tl_30dpd num_tl_90g_dpd_24m num_tl_op_past_12m pct_tl_nvr_dlq percent_bc_gt_75 pub_rec_bankruptcies tax_liens tot_hi_cred_lim total_bal_ex_mort total_bc_limit total_il_high_credit_limit revol_bal_joint sec_app_earliest_cr_line sec_app_inq_last_6mths sec_app_mort_acc sec_app_open_acc sec_app_revol_util sec_app_open_il_6m sec_app_num_rev_accts sec_app_chargeoff_within_12_mths sec_app_collections_12_mths_ex_med sec_app_mths_since_last_major_derog hardship_flag hardship_type hardship_reason hardship_status deferral_term hardship_amount hardship_start_date hardship_end_date payment_plan_start_date hardship_length hardship_dpd hardship_loan_status orig_projected_additional_accrued_interest hardship_payoff_balance_amount hardship_last_payment_amount issue_d null null 35000.0 35000 35000.0 36 months 17.27% 1252.56 D D2 Owner 10+ years RENT 107000.0 Verified Current n null null debt_consolidation Debt consolidation 900xx CA 21.88 0.0 Mar-1996 0 null 47 9 2 65692 92.7% 20.0 w 21634.04 21634.04 19973.8 19973.8 13365.96 6607.84 0.0 0.0 0.0 Aug-2017 1252.56 Sep-2017 Aug-2017 0 null 1 INDIVIDUAL null null null 0 0 86057 0 2 2 2 9 20365 88 0 0 24914 92 70900 0 12 0 2 10757 2844 94.1 0.0 0 157.0 240 27 9 0 41 null 18 null 0 2 3 4 6 9 7 11 3 9 0 0 0 2 100.0 50.0 0 2 93936 86057 48400 23036 null null null null null null null null null null null N null null null null null null null null null null null null null null Mar-2016 null null 8000.0 8000 8000.0 36 months 18.25% 290.23 D D3 Manager 9 years RENT 50000.0 Source Verified Late (31-120 days) n null null debt_consolidation Debt consolidation 907xx CA 22.0 0.0 Oct-2009 0 null null 15 0 10227 43% 25.0 w 5392.03 5392.03 4047.0 4047.0 2607.97 1439.03 0.0 0.0 0.0 Jun-2017 290.23 Sep-2017 Aug-2017 0 null 1 INDIVIDUAL null null null 0 0 33913 1 2 1 2 12 23686 78 1 5 4010 63 23800 2 2 5 7 2422 0 101.1 0.0 0 30.0 77 6 6 0 6 null 2 null 0 3 7 4 5 4 13 19 7 15 0 0 0 2 100.0 100.0 0 0 54092 33913 6500 30292 null null null null null null null null null null null N null null null null null null null null null null null null null null Mar-2016 null null 5000.0 5000 5000.0 36 months 6.97% 154.32 A A3 null n/a OWN 25000.0 Source Verified Current n null null major_purchase Major purchase 179xx PA 3.31 0.0 Aug-1988 0 null null 3 0 2246 34.6% 12.0 w 2905.82 2905.82 2465.25 2465.25 2094.18 371.07 0.0 0.0 0.0 Aug-2017 154.32 Sep-2017 Aug-2017 0 null 1 INDIVIDUAL null null null 0 0 2246 0 0 0 0 61 0 null 0 0 1199 35 6500 0 0 1 0 749 3301 26.6 0.0 0 128.0 331 108 61 2 108 null 9 null 0 1 2 2 4 2 3 8 2 3 0 0 0 0 100.0 50.0 0 0 6500 2246 4500 0 null null null nul

Output can only be rendered in Databricks

In [0]:
# -----------------------------------------------
# Uncomment and run if this folder does not exist
# -----------------------------------------------
# Configure location of loanstats_2012_2017.parquet

# Read loanstats_2012_2017.delta
data = spark.read.format("delta").load(lc_path)

# Reduce the amount of data (to run on DBCE)
#(loan_stats, loan_stats_rest) = data.randomSplit([0.01, 0.99], seed=123)

# Select only the columns needed
loan_stats = data.select("addr_state", "loan_status")

# Create loan by state
loan_by_state = data.groupBy("addr_state").count()

# Create table
loan_by_state.createOrReplaceTempView("loan_by_state")

# Display loans by state
display(loan_by_state)

addr_state count AZ 34706 SC 18102 LA 17385 MN 26664 NJ 54569 DC 3616 OR 17545 VA 42115 RI 6507 KY 14360 WY 3259 NH 7254 MI 39068 NV 20952 WI 19544 ID 1796 CA 207102 CT 22940 NE 4266 MT 4202 NC 41755 VT 3154 MD 34933 DE 4188 MO 23595 IL 59707 ME 2545 ND 1978 WA 31144 MS 7894 AL 18382 IN 24990 OH 50038 TN 23429 NM 8001 PA 51274 SD 3018 NY 122310 TX 122393 WV 4969 GA 48358 MA 33662 KS 12843 FL 103988 CO 31143 AK 3614 AR 11200 OK 13650 UT 10081 HI 7350 debt_consolidation 1 IA 2 null 18 531xx 1

Output can only be rendered in Databricks

In [0]:
%sql
select * from loan_by_state


addr_state count SC 18102 AZ 34706 LA 17385 MN 26664 NJ 54569 DC 3616 OR 17545 VA 42115 null 18 RI 6507 KY 14360 WY 3259 NH 7254 MI 39068 NV 20952 WI 19544 ID 1796 CA 207102 CT 22940 NE 4266 MT 4202 NC 41755 VT 3154 MD 34933 DE 4188 MO 23595 IL 59707 ME 2545 WA 31144 ND 1978 MS 7894 AL 18382 IN 24990 OH 50038 TN 23429 NM 8001 531xx 1 PA 51274 SD 3018 NY 122310 TX 122393 WV 4969 GA 48358 MA 33662 KS 12843 CO 31143 FL 103988 AK 3614 AR 11200 OK 13650 UT 10081 HI 7350 IA 2 debt_consolidation 1

In [0]:
%sql 
-- Current example is creating a new table instead of in-place import so will need to change this code
--DROP TABLE IF EXISTS loan_by_state;

CREATE TABLE loan_by_state
USING delta
LOCATION '/tmp/loan_by_state'
AS SELECT * FROM loan_by_state;

-- View Delta Lake table
--SELECT * FROM loan_by_state_delta

num_affected_rows num_inserted_rows

In [0]:
%sql 
DESCRIBE DETAIL delta.`/tmp/loan_by_state`

format id name description location createdAt lastModified partitionColumns numFiles sizeInBytes properties minReaderVersion minWriterVersion delta eccaf333-023a-4391-a91d-d9a66d17dba2 null null dbfs:/tmp/loan_by_state 2022-03-22T02:25:33.780+0000 2022-03-22T02:25:39.000+0000 List() 1 1374 Map() 1 2

In [0]:
%sql
describe detail loan_by_state

format id name description location createdAt lastModified partitionColumns numFiles sizeInBytes properties minReaderVersion minWriterVersion delta eccaf333-023a-4391-a91d-d9a66d17dba2 default.loan_by_state null dbfs:/tmp/loan_by_state 2022-03-22T02:25:33.780+0000 2022-03-22T02:25:39.000+0000 List() 1 1374 Map() 1 2

Output can only be rendered in Databricks

In [0]:
%sql
SELECT * FROM loan_by_state

addr_state count AZ 34706 SC 18102 LA 17385 MN 26664 NJ 54569 DC 3616 OR 17545 VA 42115 RI 6507 KY 14360 WY 3259 NH 7254 MI 39068 NV 20952 WI 19544 ID 1796 CA 207102 CT 22940 NE 4266 MT 4202 NC 41755 VT 3154 MD 34933 DE 4188 MO 23595 IL 59707 ME 2545 WA 31144 ND 1978 MS 7894 AL 18382 IN 24990 debt_consolidation 1 OH 50038 TN 23429 NM 8001 PA 51274 SD 3018 NY 122310 TX 122393 WV 4969 GA 48358 MA 33662 KS 12843 CO 31143 FL 103988 AK 3614 AR 11200 OK 13650 UT 10081 HI 7350 IA 2 null 18 531xx 1

Output can only be rendered in Databricks

## Stop the notebook before the streaming cell, in case of a "run all"

In [0]:
# dbutils.notebook.exit("stop") 

stop

In [0]:
%fs ls /tmp/loan_by_state/_delta_log/

path name size modificationTime dbfs:/tmp/loan_by_state/_delta_log/.s3-optimization-0 .s3-optimization-0 0 1647915949000 dbfs:/tmp/loan_by_state/_delta_log/.s3-optimization-1 .s3-optimization-1 0 1647915949000 dbfs:/tmp/loan_by_state/_delta_log/.s3-optimization-2 .s3-optimization-2 0 1647915949000 dbfs:/tmp/loan_by_state/_delta_log/00000000000000000000.crc 00000000000000000000.crc 520 1647915949000 dbfs:/tmp/loan_by_state/_delta_log/00000000000000000000.json 00000000000000000000.json 1391 1647915939000

## ![Delta Lake Tiny Logo](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Unified Batch and Streaming Source and Sink

These cells showcase streaming and batch concurrent queries (inserts and reads)
* This notebook will run an `INSERT` every 10s against our `loan_stats_delta` table
* We will run two streaming queries concurrently against this data
* Note, you can also use `writeStream` but this version is easier to run in DBCE

In [0]:
# Configure Delta Lake Silver Path
DELTALAKE_SILVER_PATH = "/tmp/loan_by_state"

# Remove folder if it exists
#dbutils.fs.rm(DELTALAKE_SILVER_PATH, recurse=True)

In [0]:
# Read the insertion of data
loan_by_state_readStream = spark.readStream.format("delta").load(DELTALAKE_SILVER_PATH)
loan_by_state_readStream.createOrReplaceTempView("loan_by_state_readStream")

In [0]:
%sql
select addr_state, sum(`count`) as loans from loan_by_state_readStream group by addr_state

addr_state loans SC 18102 AZ 34706 LA 17385 MN 26664 NJ 54569 DC 3616 OR 17545 null 18 VA 42115 RI 6507 WY 3259 KY 14360 NH 7254 MI 39068 NV 20952 WI 19544 ID 1796 CA 207102 NE 4266 CT 22940 MT 4202 NC 41755 VT 3154 MD 34933 DE 4188 MO 23595 IL 59707 ME 2545 WA 31144 ND 1978 MS 7894 AL 18382 IN 24990 debt_consolidation 1 OH 50038 TN 23429 NM 8001 IA 2 531xx 1 PA 51274 SD 3018 NY 122310 TX 122393 WV 4969 GA 48358 MA 33662 KS 12843 CO 31143 FL 103988 AK 3614 AR 11200 OK 13650 UT 10081 HI 7350

**Wait** until the stream is up and running before executing the code below

In [0]:
%fs ls /ml/loan_by_state_delta/_delta_log/

path name size modificationTime dbfs:/ml/loan_by_state_delta/_delta_log/.s3-optimization-0 .s3-optimization-0 0 1646624744000 dbfs:/ml/loan_by_state_delta/_delta_log/.s3-optimization-1 .s3-optimization-1 0 1646624744000 dbfs:/ml/loan_by_state_delta/_delta_log/.s3-optimization-2 .s3-optimization-2 0 1646624744000 dbfs:/ml/loan_by_state_delta/_delta_log/00000000000000000000.crc 00000000000000000000.crc 520 1646624744000 dbfs:/ml/loan_by_state_delta/_delta_log/00000000000000000000.json 00000000000000000000.json 1371 1646624740000 dbfs:/ml/loan_by_state_delta/_delta_log/00000000000000000001.crc 00000000000000000001.crc 520 1646624887000 dbfs:/ml/loan_by_state_delta/_delta_log/00000000000000000001.json 00000000000000000001.json 890 1646624886000 dbfs:/ml/loan_by_state_delta/_delta_log/00000000000000000002.crc 00000000000000000002.crc 520 1646624893000 dbfs:/ml/loan_by_state_delta/_delta_log/00000000000000000002.json 00000000000000000002.json 890 1646624892000 dbfs:/ml/loan_by_state_delta/_delta_log/00000000000000000003.crc 00000000000000000003.crc 520 1646624899000 dbfs:/ml/loan_by_state_delta/_delta_log/00000000000000000003.json 00000000000000000003.json 890 1646624899000 dbfs:/ml/loan_by_state_delta/_delta_log/00000000000000000004.crc 00000000000000000004.crc 520 1646624906000 dbfs:/ml/loan_by_state_delta/_delta_log/00000000000000000004.json 00000000000000000004.json 890 1646624905000 dbfs:/ml/loan_by_state_delta/_delta_log/00000000000000000005.crc 00000000000000000005.crc 520 1646624912000 dbfs:/ml/loan_by_state_delta/_delta_log/00000000000000000005.json 00000000000000000005.json 890 1646624911000 dbfs:/ml/loan_by_state_delta/_delta_log/00000000000000000006.crc 00000000000000000006.crc 520 1646624918000 dbfs:/ml/loan_by_state_delta/_delta_log/00000000000000000006.json 00000000000000000006.json 890 1646624917000

**Note**: Once the previous cell is finished and the state of Iowa is fully populated in the map (in cell 14), click *Cancel* in Cell 14 to stop the `readStream`.

Let's review our current set of loans using our map visualization.

In [0]:
%sql
-- Review current loans within the `loan_by_state_delta` Delta Lake table
select addr_state, sum(`count`) as loans from loan_by_state group by addr_state

addr_state loans AZ 34706 SC 18102 LA 17385 MN 26664 NJ 54569 DC 3616 OR 17545 VA 42115 RI 6507 KY 14360 WY 3259 NH 7254 MI 39068 NV 20952 WI 19544 ID 1796 CA 207102 CT 22940 NE 4266 MT 4202 NC 41755 VT 3154 MD 34933 DE 4188 MO 23595 IL 59707 ME 2545 ND 1978 WA 31144 MS 7894 AL 18382 IN 24990 OH 50038 TN 23429 NM 8001 PA 51274 SD 3018 NY 122310 TX 122393 WV 4969 GA 48358 MA 33662 KS 12843 FL 103988 CO 31143 AK 3614 AR 11200 OK 13650 UT 10081 HI 7350 debt_consolidation 1 IA 2 null 18 531xx 1

###![Delta Lake Logo Tiny](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) UPDATE Support
The data was originally supposed to be assigned to `WA` state, so let's `UPDATE` those values

In [0]:
%sql
-- Attempting to run `UPDATE` on the Parquet table

UPDATE loan_by_state SET `count` = 2700 WHERE addr_state = 'WA'

num_affected_rows 1

**Note**: This command fails because the `UPDATE` statements are not supported in Parquet, but are supported in Delta Lake.

In [0]:
%sql
-- Running `UPDATE` on the Delta Lake table
UPDATE loan_by_state_delta SET `count` = 2700 WHERE addr_state = 'WA'

In [0]:
%sql
-- Review current loans within the `loan_by_state_delta` Delta Lake table
select addr_state, sum(`count`) as loans from loan_by_state group by addr_state

addr_state loans AZ 34706 SC 18102 LA 17385 MN 26664 NJ 54569 DC 3616 OR 17545 VA 42115 null 18 RI 6507 KY 14360 WY 3259 NH 7254 MI 39068 NV 20952 WI 19544 ID 1796 CA 207102 CT 22940 NE 4266 MT 4202 NC 41755 VT 3154 MD 34933 DE 4188 MO 23595 IL 59707 ME 2545 ND 1978 WA 2700 MS 7894 AL 18382 IN 24990 debt_consolidation 1 OH 50038 TN 23429 NM 8001 IA 2 531xx 1 PA 51274 SD 3018 NY 122310 TX 122393 WV 4969 GA 48358 MA 33662 KS 12843 FL 103988 CO 31143 AK 3614 AR 11200 OK 13650 UT 10081 HI 7350

###![Delta Lake Logo Tiny](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) MERGE INTO Support

#### INSERT or UPDATE parquet: 7-step process

With a legacy data pipeline, to insert or update a table, you must:
1. Identify the new rows to be inserted
2. Identify the rows that will be replaced (i.e. updated)
3. Identify all of the rows that are not impacted by the insert or update
4. Create a new temp based on all three insert statements
5. Delete the original table (and all of those associated files)
6. "Rename" the temp table back to the original table name
7. Drop the temp table

![](https://pages.databricks.com/rs/094-YMS-629/images/merge-into-legacy.gif)


#### INSERT or UPDATE with Delta Lake

2-step process: 
1. Identify rows to insert or update
2. Use `MERGE`

In [0]:
# Let's create a simple table to merge
items = [('IA', 10), ('CA', 2500), ('OR', None)]
cols = ['addr_state', 'count']
merge_table = spark.createDataFrame(items, cols)
merge_table.createOrReplaceTempView("merge_table")
display(merge_table)

addr_state count IA 10 CA 2500 OR null

Instead of writing separate `INSERT` and `UPDATE` statements, we can use a `MERGE` statement.

In [0]:
%sql
MERGE INTO loan_by_state as d
USING merge_table as m
on d.addr_state = m.addr_state
WHEN MATCHED THEN 
  UPDATE SET *
WHEN NOT MATCHED 
  THEN INSERT *

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 3 3 0 0

In [0]:
%sql
-- Review current loans within the `loan_by_state_delta` Delta Lake table
select addr_state, sum(`count`) as loans from loan_by_state group by addr_state

addr_state loans AZ 34706 SC 18102 LA 17385 MN 26664 NJ 54569 DC 3616 OR null VA 42115 null 18 RI 6507 KY 14360 WY 3259 NH 7254 MI 39068 NV 20952 WI 19544 ID 1796 CA 2500 CT 22940 NE 4266 MT 4202 NC 41755 VT 3154 MD 34933 DE 4188 MO 23595 IL 59707 ME 2545 ND 1978 WA 2700 MS 7894 AL 18382 IN 24990 debt_consolidation 1 OH 50038 TN 23429 531xx 1 IA 10 NM 8001 PA 51274 SD 3018 NY 122310 TX 122393 WV 4969 GA 48358 MA 33662 KS 12843 CO 31143 FL 103988 AK 3614 AR 11200 OK 13650 UT 10081 HI 7350

##![Delta Lake Logo Tiny](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Schema Evolution
With the `mergeSchema` option, you can evolve your Delta Lake table schema

In [0]:
# Generate new loans with dollar amounts 
loans = sql("select addr_state, cast(rand(10)*count as bigint) as count, cast(rand(10) * 10000 * count as double) as amount from loan_by_state")
display(loans)

addr_state count amount null 3 30770.948483200224 531xx 0 8051.143958005459 AK 2087 2.087419503379271E7 AL 17418 1.7418871194415113E8 AR 2344 2.34494957488624E7 AZ 12724 1.272468510178497E8 CA 2019 2.0196720445929706E7 CO 22220 2.2220977194801E8 CT 16506 1.6506076849106088E8 DC 1133 1.1330841699721044E7 DE 3376 3.376576554596374E7 FL 11246 1.1246213442266181E8 GA 16259 1.6259086248074728E8 HI 5977 5.977979030820685E7 IA 4 47649.4287381709 ID 942 9424116.609437814 IL 57923 5.792327403374095E8 IN 15574 1.557418711708596E8 KS 6536 6.536685743897335E7 KY 7851 7.85133587971441E7 LA 245 2450782.678363302 MA 21161 2.116161170529003E8 MD 774 7744897.521623048 ME 1861 1.8612533896661248E7 MI 26654 2.665472098092273E8 MN 2630 2.6305815165823236E7 MO 1562 1.5625422630965931E7 MS 4007 4.007178126497715E7 MT 815 8157195.5744660655 NC 30047 3.0047954196542174E8 ND 852 8524464.33190985 NE 2818 2.8184186051925417E7 NH 7240 7.240058753644082E7 NJ 38163 3.816339920641493E8 NM 2897 2.89795637548179E7 NV 20577 2.0577593576675102E8 NY 69835 6.983582736874249E8 OH 30216 3.021652651672292E8 OK 12469 1.2469296286715497E8 OR null null PA 28723 2.8723497372512925E8 RI 3273 3.273360947206077E7 SC 702 7023702.504400563 SD 482 4825653.181418989 TN 1990 1.990902168781016E7 TX 84794 8.479415234848284E8 UT 2843 2.8431869630376622E7 VA 2134 2.134154710784683E7 VT 1927 1.9272573217411928E7 WA 1421 1.4219558711504081E7 WI 10777 1.0777527490104268E8 WV 322 3229722.3308450803 WY 2673 2.6735908999039173E7 debt_consolidation 0 8609.641258077847

In [0]:
DELTALAKE_SILVER_PATH = "/tmp/loan_by_state"

In [0]:
# Let's write this data out to our Delta table
loans.write.format("delta").mode("append").save(DELTALAKE_SILVER_PATH)

--------------------------------------------------------------------------- 
 AnalysisException Traceback (most recent call last)
 <command-12411789> in <module> 
 1 # Let's write this data out to our Delta table 
 ----> 2 loans . write . format ( "delta" ) . mode ( "append" ) . save ( DELTALAKE_SILVER_PATH ) 

 /databricks/spark/python/pyspark/sql/readwriter.py in save (self, path, format, mode, partitionBy, **options) 
 1134 self . _jwrite . save ( ) 
 1135 else : 
 -> 1136 self . _jwrite . save ( path ) 
 1137 
 1138 @ since ( 1.4 ) 

 /databricks/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py in __call__ (self, *args) 
 1302 
 1303 answer = self . gateway_client . send_command ( command ) 
 -> 1304 return_value = get_return_value(
 1305 answer, self.gateway_client, self.target_id, self.name)
 1306 

 /databricks/spark/python/pyspark/sql/utils.py in deco (*a, **kw) 
 121 # Hide where the exception came from that shows a non-Pythonic 
 122 # JVM exception message. 
 --> 123 raise converted from None 
 124 else : 
 125 raise 

 AnalysisException : A schema mismatch detected when writing to the Delta table (Table ID: eccaf333-023a-4391-a91d-d9a66d17dba2).
To enable schema migration using DataFrameWriter or DataStreamWriter, please set:
'.option("mergeSchema", "true")'.
For other operations, set the session configuration
spark.databricks.delta.schema.autoMerge.enabled to "true". See the documentation
specific to the operation for details.

Table schema:
root
-- addr_state: string (nullable = true)
-- count: long (nullable = true)


Data schema:
root
-- addr_state: string (nullable = true)
-- count: long (nullable = true)
-- amount: double (nullable = true)

**Note**: This command fails because the schema of our new data does not match the schema of our original data

In [0]:
# Add the mergeSchema option
loans.write.option("mergeSchema","true").format("delta").mode("append").save(DELTALAKE_SILVER_PATH)

**Note**: With the `mergeSchema` option, we can merge these different schemas together.

In [0]:
%sql
-- Review current loans within the `loan_by_state_delta` Delta Lake table
select addr_state, sum(`amount`) as amount from loan_by_state group by addr_state order by sum(`amount`) desc limit 10

addr_state amount TX 8.479415234848284E8 NY 6.983582736874249E8 IL 5.792327403374095E8 NJ 3.816339920641493E8 OH 3.021652651672292E8 NC 3.0047954196542174E8 PA 2.8723497372512925E8 MI 2.665472098092273E8 CO 2.2220977194801E8 MA 2.116161170529003E8

## ![Delta Lake Tiny Logo](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Let's Travel back in Time!
Databricks Delta’s time travel capabilities simplify building data pipelines for the following use cases. 

* Audit Data Changes
* Reproduce experiments & reports
* Rollbacks

As you write into a Delta table or directory, every operation is automatically versioned.

You can query by:
1. Using a timestamp
1. Using a version number

using Python, Scala, and/or Scala syntax; for these examples we will use the SQL syntax.  

For more information, refer to [Introducing Delta Time Travel for Large Scale Data Lakes](https://databricks.com/blog/2019/02/04/introducing-delta-time-travel-for-large-scale-data-lakes.html)

### ![Delta Lake Tiny Logo](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Review Delta Lake Table History
All the transactions for this table are stored within this table including the initial set of insertions, update, delete, merge, and inserts with schema modification

In [0]:
%sql
DESCRIBE HISTORY loan_by_state

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata 3 2022-03-22T04:27:18.000+0000 100708 vini.jaiswal@databricks.com WRITE Map(mode -> Append, partitionBy -> []) null List(12411746) 0804-214524-boded127 2 WriteSerializable false Map(numFiles -> 1, numOutputBytes -> 1973, numOutputRows -> 54) null 2 2022-03-22T04:24:48.000+0000 100708 vini.jaiswal@databricks.com MERGE Map(predicate -> (d.`addr_state` = m.`addr_state`), matchedPredicates -> [{"actionType":"update"}], notMatchedPredicates -> [{"actionType":"insert"}]) null List(12411746) 0804-214524-boded127 1 WriteSerializable false Map(numTargetRowsCopied -> 51, numTargetRowsDeleted -> 0, numTargetFilesAdded -> 1, executionTimeMs -> 1914, numTargetRowsInserted -> 0, scanTimeMs -> 991, numTargetRowsUpdated -> 3, numOutputRows -> 54, numTargetChangeFilesAdded -> 0, numSourceRows -> 3, numTargetFilesRemoved -> 1, rewriteTimeMs -> 764) null 1 2022-03-22T04:24:03.000+0000 100708 vini.jaiswal@databricks.com UPDATE Map(predicate -> (addr_state#17416 = WA)) null List(12411746) 0804-214524-boded127 0 WriteSerializable false Map(numRemovedFiles -> 1, numCopiedRows -> 53, numAddedChangeFiles -> 0, executionTimeMs -> 1363, scanTimeMs -> 952, numAddedFiles -> 1, numUpdatedRows -> 1, rewriteTimeMs -> 411) null 0 2022-03-22T02:25:39.000+0000 100708 vini.jaiswal@databricks.com CREATE TABLE AS SELECT Map(isManaged -> false, description -> null, partitionBy -> [], properties -> {}) null List(12411746) 0318-151752-abed99 null WriteSerializable true Map(numFiles -> 1, numOutputRows -> 54, numOutputBytes -> 1374) null

### ![Delta Lake Tiny Logo](https://pages.databricks.com/rs/094-YMS-629/images/delta-lake-tiny-logo.png) Time Travel via Version Number
Below are SQL syntax examples of Delta Time Travel by using a Version Number

In [0]:
%sql
SELECT * FROM loan_by_state VERSION AS OF 0

addr_state count AZ 34706 SC 18102 LA 17385 MN 26664 NJ 54569 DC 3616 OR 17545 VA 42115 RI 6507 KY 14360 WY 3259 NH 7254 MI 39068 NV 20952 WI 19544 ID 1796 CA 207102 CT 22940 NE 4266 MT 4202 NC 41755 VT 3154 MD 34933 DE 4188 MO 23595 IL 59707 ME 2545 ND 1978 WA 31144 MS 7894 AL 18382 IN 24990 OH 50038 TN 23429 NM 8001 PA 51274 SD 3018 NY 122310 TX 122393 WV 4969 GA 48358 MA 33662 KS 12843 FL 103988 CO 31143 AK 3614 AR 11200 OK 13650 UT 10081 HI 7350 debt_consolidation 1 IA 2 null 18 531xx 1

In [0]:
%sql
SELECT * FROM loan_by_state VERSION AS OF 2

addr_state count null 18 531xx 1 AK 3614 AL 18382 AR 11200 AZ 34706 CA 2500 CO 31143 CT 22940 DC 3616 DE 4188 FL 103988 GA 48358 HI 7350 IA 10 ID 1796 IL 59707 IN 24990 KS 12843 KY 14360 LA 17385 MA 33662 MD 34933 ME 2545 MI 39068 MN 26664 MO 23595 MS 7894 MT 4202 NC 41755 ND 1978 NE 4266 NH 7254 NJ 54569 NM 8001 NV 20952 NY 122310 OH 50038 OK 13650 OR null PA 51274 RI 6507 SC 18102 SD 3018 TN 23429 TX 122393 UT 10081 VA 42115 VT 3154 WA 2700 WI 19544 WV 4969 WY 3259 debt_consolidation 1

## Run Our Model
Let's run a simple linear regression model to predict the number of loans based on the population of the state
* The following shell statements downloads the us_census_2020 data that we will join with the `loan_by_state_delta` table

In [0]:
%sh mkdir -p /dbfs/tmp/data-council/census/ && wget -O /dbfs/tmp/data-council/census/us_census_2010.csv https://pages.databricks.com/rs/094-YMS-629/images/us_census_2010.csv && ls -al /dbfs/tmp/data-council/census/

--2022-03-22 04:30:57-- https://pages.databricks.com/rs/094-YMS-629/images/us_census_2010.csv
Resolving pages.databricks.com (pages.databricks.com)... 104.17.73.206, 104.17.74.206, 104.17.70.206, ...
Connecting to pages.databricks.com (pages.databricks.com)|104.17.73.206|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 591 [text/plain]
Saving to: ‘/dbfs/tmp/data-council/census/us_census_2010.csv’

 0K 100% 201K=0.003s

2022-03-22 04:30:57 (201 KB/s) - ‘/dbfs/tmp/data-council/census/us_census_2010.csv’ saved [591/591]

total 9
drwxrwxrwx 2 root root 4096 Mar 22 2022 .
drwxrwxrwx 2 root root 4096 Mar 22 04:30 ..
-rwxrwxrwx 1 root root 591 Mar 22 2022 us_census_2010.csv

In [0]:
dbutils.fs.cp("file:/dbfs/tmp/data-council/census", "dbfs:/tmp/sais_eu_19_demo/census/", recurse=True)

Out[8]: True

### Notes
If you forgot to install `mlflow` and `yellowbrick` on your cluster, instead of re-running everything all over again:
* Note that the Delta Lake table is stored in `DELTALAKE_SILVERPATH` or `/ml/loan_by_state_delta`
* You can add the libraries, restart the cluster and then start reading the data from the following cells (instead of rerunning everything all over again)
* Just uncomment the cell below to reconnect to your Delta Table

In [0]:
%pip install mlflow yellowbrick

Python interpreter will be restarted.
Collecting mlflow
 Downloading mlflow-1.24.0-py3-none-any.whl (16.5 MB)
Collecting yellowbrick
 Downloading yellowbrick-1.4-py3-none-any.whl (274 kB)
Requirement already satisfied: pytz in /databricks/python3/lib/python3.8/site-packages (from mlflow) (2020.5)
Requirement already satisfied: Flask in /databricks/python3/lib/python3.8/site-packages (from mlflow) (1.1.2)
Collecting sqlalchemy
 Downloading SQLAlchemy-1.4.32-cp38-cp38-manylinux_2_5_x86_64.manylinux1_x86_64.manylinux_2_17_x86_64.manylinux2014_x86_64.whl (1.6 MB)
Requirement already satisfied: scipy in /databricks/python3/lib/python3.8/site-packages (from mlflow) (1.6.2)
Collecting alembic
 Downloading alembic-1.7.7-py3-none-any.whl (210 kB)
Requirement already satisfied: pandas in /databricks/python3/lib/python3.8/site-packages (from mlflow) (1.2.4)
Requirement already satisfied: sqlparse>=0.3.1 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (0.4.1)
Requirement already satisfied: gitpython>=2.1.0 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (3.1.12)
Requirement already satisfied: numpy in /databricks/python3/lib/python3.8/site-packages (from mlflow) (1.19.2)
Requirement already satisfied: databricks-cli>=0.8.7 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (0.14.3)
Requirement already satisfied: packaging in /databricks/python3/lib/python3.8/site-packages (from mlflow) (20.9)
Requirement already satisfied: protobuf>=3.7.0 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (3.17.2)
Requirement already satisfied: requests>=2.17.3 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (2.25.1)
Requirement already satisfied: cloudpickle in /databricks/python3/lib/python3.8/site-packages (from mlflow) (1.6.0)
Requirement already satisfied: click>=7.0 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (7.1.2)
Requirement already satisfied: gunicorn in /databricks/python3/lib/python3.8/site-packages (from mlflow) (20.0.4)
Collecting docker>=4.0.0
 Downloading docker-5.0.3-py2.py3-none-any.whl (146 kB)
Collecting querystring-parser
 Downloading querystring_parser-1.2.4-py2.py3-none-any.whl (7.9 kB)
Requirement already satisfied: pyyaml>=5.1 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (5.4.1)
Requirement already satisfied: importlib-metadata!=4.7.0,>=3.7.0 in /databricks/python3/lib/python3.8/site-packages (from mlflow) (3.10.0)
Requirement already satisfied: entrypoints in /databricks/python3/lib/python3.8/site-packages (from mlflow) (0.3)
Collecting prometheus-flask-exporter
 Downloading prometheus_flask_exporter-0.19.0-py3-none-any.whl (18 kB)
Requirement already satisfied: six>=1.10.0 in /databricks/python3/lib/python3.8/site-packages (from databricks-cli>=0.8.7->mlflow) (1.15.0)
Requirement already satisfied: tabulate>=0.7.7 in /databricks/python3/lib/python3.8/site-packages (from databricks-cli>=0.8.7->mlflow) (0.8.7)
Requirement already satisfied: websocket-client>=0.32.0 in /databricks/python3/lib/python3.8/site-packages (from docker>=4.0.0->mlflow) (0.57.0)
Requirement already satisfied: gitdb<5,>=4.0.1 in /databricks/python3/lib/python3.8/site-packages (from gitpython>=2.1.0->mlflow) (4.0.7)
Requirement already satisfied: smmap<5,>=3.0.1 in /databricks/python3/lib/python3.8/site-packages (from gitdb<5,>=4.0.1->gitpython>=2.1.0->mlflow) (3.0.5)
Requirement already satisfied: zipp>=0.5 in /databricks/python3/lib/python3.8/site-packages (from importlib-metadata!=4.7.0,>=3.7.0->mlflow) (3.4.1)
Requirement already satisfied: certifi>=2017.4.17 in /databricks/python3/lib/python3.8/site-packages (from requests>=2.17.3->mlflow) (2020.12.5)
Requirement already satisfied: chardet<5,>=3.0.2 in /databricks/python3/lib/python3.8/site-packages (from requests>=2.17.3->mlflow) (4.0.0)
Requirement already satisfied: urllib3<1.27,>=1.21.1 in /databricks/python3/lib/python3.8/site-packages (from requests>=2.17.3->mlflow) (1.25.11)
Req

In [0]:
# Recreate loan_by_state_delta view
spark.read.format("delta").load("/tmp/loan_by_state").createOrReplaceTempView("loan_by_state")
# Check data
display(spark.sql("select count(1) from loan_by_state"))

count(1) 108

In [0]:
# Include census data
census = spark.read.csv('/tmp/data-council/census/us_census_2010.csv', sep=',', inferSchema=True, header=True)
census.createOrReplaceTempView("census")

# Data versions (0, 2, 3)
dfv0 = spark.sql("select c.Population, l.count as label from (select addr_state as State, count from loan_by_state  version as of 0) l left outer join census c on c.State = l.State")
dfv2 = spark.sql("select c.Population, l.count as label from (select addr_state as State, count from loan_by_state  version as of 2) l left outer join census c on c.State = l.State")
dfv3 = spark.sql("select c.Population, l.count as label from (select addr_state as State, count from loan_by_state  version as of 3 where count is not null) l left outer join census c on c.State = l.State")

In [0]:
# Import MLflow
import mlflow
import mlflow.spark
#print("MLflow Version: %s" % mlflow.__version__)

# Display Residuals (yellowbrick)
def displayResiduals(train, test):
  from sklearn.linear_model import Ridge
  from yellowbrick.regressor import ResidualsPlot

  # define feature columns
  featureColumns = ['Population']

  # Create pandas DataFrames
  pdf_train = train.toPandas()
  pdf_test = test.toPandas()

  # Convert to X, y train and test values
  X_train = pdf_train[['Population']].to_numpy()
  y_train = pdf_train[['label']].to_numpy().flatten()
  X_test = pdf_test[['Population']].to_numpy()
  y_test = pdf_test[['label']].to_numpy().flatten()  
  
  # Instantiate the linear model and visualizer
  ridge = Ridge()
  visualizer = ResidualsPlot(ridge)

  # Visualize
  visualizer.fit(X_train, y_train)  # Fit the training data to the model
  visualizer.score(X_test, y_test)  # Evaluate the model on the test data
  visualizer.show(outpath="ridge-model-residuals.png")
  #fig=visualizer.poof()             # Draw/show/poof the data
  
# Predict Loan Count (based on state population)
def predictLoanCount(df, data_version):
  from pyspark.ml.linalg import Vectors
  from pyspark.ml.feature import VectorAssembler
  from pyspark.ml.regression import LinearRegression
  from pyspark.ml.evaluation import RegressionEvaluator
  
  # assemble vector
  assembler = VectorAssembler(
    inputCols=["Population"],
    outputCol="features")
  output = assembler.transform(df)

  # Log mlflow
  with mlflow.start_run() as run:  
    # Define LinearRegression algorithm
    lr = LinearRegression(maxIter=10, regParam=0.0, elasticNetParam=0.8)
    model = lr.fit(output)  

    # Calculate predictions
    predictions = model.transform(output)

    # calculate RMSE
    evaluator = RegressionEvaluator(metricName="rmse")
    RMSE = evaluator.evaluate(predictions)
    #print("Model: Root Mean Squared Error = " + str(RMSE))

    # Log Parameters
    mlflow.log_param("data version", data_version)
    mlflow.log_metric("RMSE", RMSE)

    # Log Model
    mlflow.spark.log_model(model, "model") 
    
    # Save if not data_version is "v0"
    if (data_version != 'v0'):
      # Log artifacts (output files)
      mlflow.log_artifact("ridge-model-residuals.png")
  
  # return predictions DataFrame
  #return predictions

In [0]:
# Calculate predictions
# Initial version of data (v0)
predictLoanCount(dfv0, 'v0')

# Version 6 (after streaming of Iowa data)
displayResiduals(dfv0, dfv2)
predictLoanCount(dfv2, 'v2')

# Version 9 (after correction of data: update, delete, merge)
displayResiduals(dfv0, dfv3)
predictLoanCount(dfv3, 'v3')

--------------------------------------------------------------------------- 
 Py4JJavaError Traceback (most recent call last)
 <command-12411808> in <module> 
 1 # Calculate predictions 
 2 # Initial version of data (v0) 
 ----> 3 predictLoanCount ( dfv0 , 'v0' ) 
 4 
 5 # Version 6 (after streaming of Iowa data) 

 <command-12411807> in predictLoanCount (df, data_version) 
 49 # Define LinearRegression algorithm 
 50 lr = LinearRegression ( maxIter = 10 , regParam = 0.0 , elasticNetParam = 0.8 ) 
 ---> 51 model = lr . fit ( output ) 
 52 
 53 # Calculate predictions 

 /databricks/python_shell/dbruntime/MLWorkloadsInstrumentation/_pyspark.py in patched_method (self, *args, **kwargs) 
 28 call_succeeded = False 
 29 try : 
 ---> 30 result = original_method ( self , * args , ** kwargs ) 
 31 call_succeeded = True 
 32 return result

 /local_disk0/.ephemeral_nfs/envs/pythonEnv-44ae8c41-7ae3-45e9-8757-d4ccb74efc0f/lib/python3.8/site-packages/mlflow/utils/autologging_utils/safety.py in safe_patch_function (*args, **kwargs) 
 433 reroute_warnings = False , 
 434 ):
 --> 435 return original ( * args , ** kwargs ) 
 436 
 437 # Whether or not the original / underlying function has been called during the 

 /databricks/spark/python/pyspark/ml/base.py in fit (self, dataset, params) 
 159 return self . copy ( params ) . _fit ( dataset ) 
 160 else : 
 --> 161 return self . _fit ( dataset ) 
 162 else : 
 163 raise ValueError("Params must be either a param map or a list/tuple of param maps, "

 /databricks/spark/python/pyspark/ml/wrapper.py in _fit (self, dataset) 
 333 
 334 def _fit ( self , dataset ) : 
 --> 335 java_model = self . _fit_java ( dataset ) 
 336 model = self . _create_model ( java_model ) 
 337 return self . _copyValues ( model ) 

 /databricks/spark/python/pyspark/ml/wrapper.py in _fit_java (self, dataset) 
 330 """
 331 self . _transfer_params_to_java ( ) 
 --> 332 return self . _java_obj . fit ( dataset . _jdf ) 
 333 
 334 def _fit ( self , dataset ) : 

 /databricks/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py in __call__ (self, *args) 
 1302 
 1303 answer = self . gateway_client . send_command ( command ) 
 -> 1304 return_value = get_return_value(
 1305 answer, self.gateway_client, self.target_id, self.name)
 1306 

 /databricks/spark/python/pyspark/sql/utils.py in deco (*a, **kw) 
 115 def deco ( * a , ** kw ) : 
 116 try : 
 --> 117 return f ( * a , ** kw ) 
 118 except py4j . protocol . Py4JJavaError as e : 
 119 converted = convert_exception ( e . java_exception ) 

 /databricks/spark/python/lib/py4j-0.10.9-src.zip/py4j/protocol.py in get_return_value (answer, gateway_client, target_id, name) 
 324 value = OUTPUT_CONVERTER [ type ] ( answer [ 2 : ] , gateway_client ) 
 325 if answer [ 1 ] == REFERENCE_TYPE : 
 --> 326 raise Py4JJavaError(
 327 "An error occurred while calling {0}{1}{2}.\n" . 
 328 format(target_id, ".", name), value)

 Py4JJavaError : An error occurred while calling o535.fit.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 0 in stage 243.0 failed 4 times, most recent failure: Lost task 0.3 in stage 243.0 (TID 265) (10.0.239.27 executor 0): org.apache.spark.SparkException: Failed to execute user defined function(VectorAssembler$$Lambda$9414/930836871: (struct<Population:double>) => struct<type:tinyint,size:int,indices:array<int>,values:array<double>>)
	at org.apache.spark.sql.catalyst.expressions.GeneratedClass$GeneratedIteratorForCodegenStage2.processNext(Unknown Source)
	at org.apache.spark.sql.execution.BufferedRowIterator.hasNext(BufferedRowIterator.java:43)
	at org.apache.spark.sql.execution.WholeStageCodegenExec$$anon$1.hasNext(WholeStageCodegenExec.scala:757)
	at scala.collection.Iterator$$anon$10.hasNext(Iterator.scala:458)
	at scala.collection.Iterator$$anon$10.hasNext(Iterator.scala:458)
	at scala.collection.Iterator$$anon$10.hasNext(Iterator.scala:458)
	at scala.collection.Iterator.foreach(Iterator.scala:941)
	at scala.collection.Iterator.foreach

#### Review RMSE and Residuals
* Review the RMSE values via the MLflow Sidebar